In [1]:
# Notebook parameters. Values here are for development only and 
# will be overridden when running via snakemake and papermill.
cohort_id = "CD-NU_Gbadolite_gamb_2015_Q3"
# cohort_id = 'ML-2_Kati_colu_2014_Q3'
# cohort_id = 'CI-LG_Agneby-Tiassa_colu_2012'
cohorts_analysis = "20230223"
contigs = ['2RL', '3RL', 'X']
sample_sets = "3.0"
min_cohort_size = 20
max_cohort_size = 50
h12_calibration_contig = '3L'
use_gcs_cache = False
dask_scheduler = "threads"

In [2]:
# Parameters
min_cohort_size = 20
max_cohort_size = 50
sample_sets = ["3.0"]
contigs = ["2RL", "3RL", "X"]
cohorts_analysis = "20230223"
h12_calibration_contig = "3L"
h12_signal_detection_min_delta_aic = 1000
h12_signal_detection_min_stat_max = 0.1
h12_signal_detection_gflanks = [6]
use_gcs_cache = False
dask_scheduler = "single-threaded"
cohort_id = "BF-09_Houet_colu_2012_Q3"


In [3]:
from IPython.display import Markdown, HTML
import malariagen_data
import numpy as np
import pandas as pd
from pyprojroot import here
import yaml
import dask
dask.config.set(scheduler=dask_scheduler);
from textwrap import dedent

import geopandas as gpd
import bokeh.layouts as bklay
import bokeh.plotting as bkplt
import bokeh.models as bkmod
import plotly.express as px

from bokeh.io import output_notebook # enables plot interface in J notebook

# N.B., do not add the "remove-output" tag to this cell!!! If you do,
# the bokeh javascript libraries will not get loaded in the generated
# HTML page. The call to output_notebook() injects javascript in the
# cell output which triggers the bokeh javascript libraries to be loaded
# in the page.
output_notebook(hide_banner=True)

# Burkina Faso / Houet / coluzzii / 2012 / Q3

In [4]:
# Load cohorts to find sample query to select samples for this cohort.

df_cohorts = gpd.read_file(here() / "build" / "final_cohorts.geojson").set_index("cohort_id")
cohort = df_cohorts.loc[cohort_id]
cohort

cohort_size                                                          78
country                                                    Burkina Faso
admin1_iso                                                        BF-09
admin1_name                                               Hauts-Bassins
admin2_name                                                       Houet
taxon                                                          coluzzii
year                                                               2012
quarter                                                               3
cohort_label                Burkina Faso / Houet / coluzzii / 2012 / Q3
sample_query          cohort_admin2_quarter == 'BF-09_Houet_colu_201...
latitude                                                      11.223768
longitude                                                      -4.35639
h12_window_size                                                  1000.0
country_alpha2                                                  

In [5]:
# Initialise access to MalariaGEN data.

extra_params = dict()
if use_gcs_cache:
    extra_params["url"] = "simplecache::gs://vo_agam_release"
    extra_params["simplecache"] = dict(cache_storage=(here() / "gcs_cache").as_posix())

ag3 = malariagen_data.Ag3(
    # Pin the version of the cohorts analysis for reproducibility.
    cohorts_analysis=cohorts_analysis,
    results_cache=(here() / "malariagen_data_cache").as_posix(),
    **extra_params,
)
ag3

<MalariaGEN Ag3 API client>
Storage URL             : gs://vo_agam_release/
Data releases available : 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8
Results cache           : /home/sanjaynagi/selection-atlas/malariagen_data_cache
Cohorts analysis        : 20230223
AIM analysis            : 20220528
Site filters analysis   : dt_20200416
Software version        : malariagen_data 7.13.0
Client location         : unknown
---
Please note that data are subject to terms of use,
for more information see https://www.malariagen.net/data
or contact data@malariagen.net. For API documentation see 
https://malariagen.github.io/vector-data/ag3/api.html

In [6]:
# Load sample metadata for this cohort.

df_samples = ag3.sample_metadata(sample_query=cohort['sample_query'])
df_samples

sample_id partner_sample_id  contributor       country      location  \
0    AB0087-C             BF3-3  Austin Burt  Burkina Faso  Bana Village   
1    AB0088-C             BF3-5  Austin Burt  Burkina Faso  Bana Village   
2   AB0089-Cx             BF3-8  Austin Burt  Burkina Faso  Bana Village   
3    AB0090-C            BF3-10  Austin Burt  Burkina Faso  Bana Village   
4    AB0091-C            BF3-12  Austin Burt  Burkina Faso  Bana Village   
..        ...               ...          ...           ...           ...   
73  AB0266-Cx           BF12-15  Austin Burt  Burkina Faso          Pala   
74   AB0267-C           BF12-16  Austin Burt  Burkina Faso          Pala   
75   AB0276-C           BF12-27  Austin Burt  Burkina Faso          Pala   
76   AB0279-C           BF12-30  Austin Burt  Burkina Faso          Pala   
77  AB0282-Cx           BF12-33  Austin Burt  Burkina Faso          Pala   

    year  month  latitude  longitude sex_call  ...    admin1_name admin1_iso  \
0   2012      7    11.233     -4.472        F  ...  Hauts-Bassins      BF-09   
1   2012      7    11.233     -4.472        F  ...  Hauts-Bassins      BF-09   
2   2012      7    11.233     -4.472        F  ...  Hauts-Bassins      BF-09   
3   2012      7    11.233     -4.472        F  ...  Hauts-Bassins      BF-09   
4   2012      7    11.233     -4.472        F  ...  Hauts-Bassins      BF-09   
..   ...    ...       ...        ...      ...  ...            ...        ...   
73  2012      7    11.151     -4.235        F  ...  Hauts-Bassins      BF-09   
74  2012      7    11.151     -4.235        F  ...  Hauts-Bassins      BF-09   
75  2012      7    11.151     -4.235        F  ...  Hauts-Bassins      BF-09   
76  2012      7    11.151     -4.235        F  ...  Hauts-Bassins      BF-09   
77  2012      7    11.151     -4.235        F  ...  Hauts-Bassins      BF-09   

    admin2_name     taxon  cohort_admin1_year  cohort_admin1_month  \
0         Houet  coluzzii     BF-09_colu_2012   BF-09_colu_2012_07   
1         Houet  coluzzii     BF-09_colu_2012   BF-09_colu_2012_07   
2         Houet  coluzzii     BF-09_colu_2012   BF-09_colu_2012_07   
3         Houet  coluzzii     BF-09_colu_2012   BF-09_colu_2012_07   
4         Houet  coluzzii     BF-09_colu_2012   BF-09_colu_2012_07   
..          ...       ...                 ...                  ...   
73        Houet  coluzzii     BF-09_colu_2012   BF-09_colu_2012_07   
74        Houet  coluzzii     BF-09_colu_2012   BF-09_colu_2012_07   
75        Houet  coluzzii     BF-09_colu_2012   BF-09_colu_2012_07   
76        Houet  coluzzii     BF-09_colu_2012   BF-09_colu_2012_07   
77        Houet  coluzzii     BF-09_colu_2012   BF-09_colu_2012_07   

   cohort_admin1_quarter     cohort_admin2_year       cohort_admin2_month  \
0     BF-09_colu_2012_Q3  BF-09_Houet_colu_2012  BF-09_Houet_colu_2012_07   
1     BF-09_colu_2012_Q3  BF-09_Houet_colu_2012  BF-09_Houet_colu_2012_07   
2     BF-09_colu_2012_Q3  BF-09_Houet_colu_2012  BF-09_Houet_colu_2012_07   
3     BF-09_colu_2012_Q3  BF-09_Houet_colu_2012  BF-09_Houet_colu_2012_07   
4     BF-09_colu_2012_Q3  BF-09_Houet_colu_2012  BF-09_Houet_colu_2012_07   
..                   ...                    ...                       ...   
73    BF-09_colu_2012_Q3  BF-09_Houet_colu_2012  BF-09_Houet_colu_2012_07   
74    BF-09_colu_2012_Q3  BF-09_Houet_colu_2012  BF-09_Houet_colu_2012_07   
75    BF-09_colu_2012_Q3  BF-09_Houet_colu_2012  BF-09_Houet_colu_2012_07   
76    BF-09_colu_2012_Q3  BF-09_Houet_colu_2012  BF-09_Houet_colu_2012_07   
77    BF-09_colu_2012_Q3  BF-09_Houet_colu_2012  BF-09_Houet_colu_2012_07   

       cohort_admin2_quarter  
0   BF-09_Houet_colu_2012_Q3  
1   BF-09_Houet_colu_2012_Q3  
2   BF-09_Houet_colu_2012_Q3  
3   BF-09_Houet_colu_2012_Q3  
4   BF-09_Houet_colu_2012_Q3  
..                       ...  
73  BF-09_Houet_colu_2012_Q3  
74  BF-09_Houet_colu_2012_Q3  
75  BF-09_Houet_colu_2012_Q3  
76  BF-09_Houet_colu_2012_Q3  
77  BF-09_Houet_colu_20

In [7]:
# Determine collection dates.

df_collection_dates = (
    df_samples
    .groupby(["year", "month"])
    .size()
    .reset_index()
    .rename(columns={0: 'count'})
)
df_collection_dates

year  month  count
0  2012      7     78

In [8]:
# Determine first and last collection months.

min_month = df_collection_dates["month"].min()
max_month = df_collection_dates["month"].max()

if min_month < 0:
    start_month = end_month = None
else:
    start_month = pd.to_datetime(min_month, format="%m").month_name()
    end_month = pd.to_datetime(max_month, format="%m").month_name()
    
start_month, end_month

('July', 'July')

In [9]:
# Determine unique collection locations.

df_locations = df_samples[["location", "longitude", "latitude"]].drop_duplicates()
df_locations

location  longitude  latitude
0     Bana Village     -4.472    11.233
20  Souroukoudinga     -4.235    11.238
41            Pala     -4.235    11.151

In [10]:
# Extract provenance information about the samples.

df_contributors = df_samples[["release", "sample_set", "contributor"]].drop_duplicates()
df_contributors["study"] = df_contributors.apply(
    lambda v: "Ag1000G" if v["sample_set"].startswith("AG1000G") else "TODO",
    axis="columns"
)
df_contributors["release"] = df_contributors["release"].apply(
    lambda v: f"Ag{v}"
)
df_contributors.rename(columns={
    "contributor": "Contributor",
    "study": "Study",
    "release": "Data release",
    "sample_set": "Sample set",
}, inplace=True)
df_contributors.set_index(["Contributor", "Study", "Data release"], inplace=True)
df_contributors

Sample set
Contributor Study   Data release              
Austin Burt Ag1000G Ag3.0         AG1000G-BF-A

In [11]:
# Build a paragraph with summary information about the samples in this cohort.

n_locations = len(df_locations)

summary_info = f"""This cohort comprises {cohort['cohort_size']:,} samples from the 
*{cohort['taxon']}* taxon, collected from {n_locations} locations within the administrative 
division of {cohort['admin2_name']}, {cohort['admin1_name']}, {cohort['country']}."""

if start_month and start_month == end_month:
    summary_info += f""" Collections were made in {start_month} {cohort['year']}."""
elif start_month:
    summary_info += f""" Collections were made between {start_month} and {end_month} in {cohort['year']}."""
else:
    summary_info += f""" Collections were made in {cohort['year']}."""
    
display(Markdown(summary_info))


This cohort comprises 78 samples from the 
*coluzzii* taxon, collected from 3 locations within the administrative 
division of Houet, Hauts-Bassins, Burkina Faso. Collections were made in July 2012.

## Selection scans

In [12]:
# load signals to overlay on H12 plots
import pandas as pd

df_signals_contigs = []
for contig in contigs:

    try:
        df_signals_contig = pd.read_csv(here() / "build/h12-signal-detection/" / f"{cohort_id}_{contig}.csv")
    except pd.errors.EmptyDataError:
        df_signals_contig = pd.DataFrame()
    df_signals_contigs.append(df_signals_contig)  
    
df_signals = pd.concat(df_signals_contigs)

# Add extra columns to help with overlaying signals on plots.
df_signals["bottom"] = 0
df_signals["top"] = 1

df_signals

cohort_id contig     gcenter   pcenter  delta_i  stat_max  \
0  BF-09_Houet_colu_2012_Q3    2RL   40.465951  20232976     1080    0.1064   
1  BF-09_Houet_colu_2012_Q3    2RL   49.731887  24865944     1881    0.3112   
2  BF-09_Houet_colu_2012_Q3    2RL   56.944442  28472221     5407    0.4058   
3  BF-09_Houet_colu_2012_Q3    2RL   81.899071  40949536     3242    0.1936   
4  BF-09_Houet_colu_2012_Q3    2RL  120.963003  64252133     3460    0.9220   
5  BF-09_Houet_colu_2012_Q3    2RL  166.461381  87001322     6491    0.3440   
0  BF-09_Houet_colu_2012_Q3    3RL   57.209967  28604984     5752    0.3078   
1  BF-09_Houet_colu_2012_Q3    3RL  104.625655  52811961     1010    0.4142   
0  BF-09_Houet_colu_2012_Q3      X   18.473418   9236709     3494    0.1302   
1  BF-09_Houet_colu_2012_Q3      X   30.502500  15251250     6458    0.9412   

     gpos_max  ppos_max  focus_gstart  focus_gstop  ...      skew  decay_left  \
0   40.480698  20240349     40.295975    40.550940  ...  0.500000    0.679906   
1   49.703554  24851777     49.671572    49.762045  ...  0.500000    0.241263   
2   56.992114  28496057     56.839693    57.029901  ...  0.146805    0.418992   
3   81.833786  40916893     81.835686    81.973574  ... -0.116585    0.253540   
4  120.440135  63948403    120.658807   121.115101  ...  0.500000    1.216784   
5  166.430596  86985929    166.294040   166.545052  ...  0.500000    0.669363   
0   57.194894  28597447     57.107924    57.263632  ...  0.463559    0.408172   
1  104.623588  52807827    104.470297   104.936372  ... -0.500000    0.621434   
0   18.473710   9236855     18.435930    18.493144  ...  0.463161    0.149952   
1   30.631892  15315946     30.339552    30.741312  ... -0.275733    0.651792   

   decay_right  baseline           aic           bic       rss  constant_aic  \
0     0.339953  0.019010 -19543.709465 -19515.571743  0.150728 -18462.970361   
1     0.120631  0.030709 -16812.416402 -16784.203781  0.653259 -14930.881366   
2     0.341838  0.032930 -16937.701610 -16909.561454  0.538469 -11530.093739   
3     0.298014  0.022158 -15945.395689 -15918.420151  0.090220 -12702.892615   
4     0.608392  0.014315  -8038.532938  -8011.877636  7.847903  -4578.017818   
5     0.334682  0.013249 -17651.473986 -17623.575592  0.236814 -11159.516381   
0     0.214661  0.013684 -17237.390862 -17209.749203  0.174739 -11485.107047   
1     1.242867  0.038533  -9126.899590  -9100.671315  2.072195  -8116.812500   
0     0.078904  0.016439 -20749.142578 -20721.420917  0.032086 -17255.036890   
1     0.955249  0.019270 -12417.283542 -12389.472734  3.013417  -5958.332401   

   bottom  top  
0       0    1  
1       0    1  
2       0    1  
3       0    1  
4       0    1  
5       0    1  
0       0    1  
1       0    1  
0       0    1  
1       0    1  

[10 rows x 32 columns]

In [13]:
# load window sizes 
h12_calibration_dir = "build/h12-calibration"
with open(here() / h12_calibration_dir / f"{cohort_id}.yaml") as h12_calibration_file:
    h12_calibration_params = yaml.safe_load(h12_calibration_file)
h12_window_size = h12_calibration_params["h12_window_size"]
g123_calibration_dir = "build/g123-calibration"
with open(here() / g123_calibration_dir / f"{cohort_id}.yaml") as g123_calibration_file:
    g123_calibration_params = yaml.safe_load(g123_calibration_file)
g123_window_size = g123_calibration_params["g123_window_size"]

if cohort.taxon == 'arabiensis':
    phasing_analysis = 'arab'
else:
    phasing_analysis = 'gamb_colu'

ihs_window_size = 100

def plot_h12_g123_ihs_tracks(
        contig, 
        df_signals,
        sizing_mode='stretch_width', 
        show=False, 
        width=800, 
        track_height=150,
        genes_height=90,
    ):

    sample_query = cohort["sample_query"]
    
    fig1 = ag3.plot_h12_gwss_track(
        contig=contig, 
        window_size=h12_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        show=show,
        width=width,
        height=track_height,
    )
    fig1.xaxis.visible = False
        
    if not df_signals.empty:
        df = df_signals.query("contig == @contig")
        center_xs = [np.array([row.pcenter, row.pcenter]) for idx, row in df.iterrows()]
        center_ys = [np.array([0, 1]) for idx, row in df.iterrows()]
        source = bkmod.ColumnDataSource(data={
            'cohort': df.cohort_id,
            'chromosome': df.contig,
            'score': df.delta_i.astype(int),
            'peak_start': df.span2_pstart,
            'peak_stop': df.span2_pstop,
            'focus_start': df.focus_pstart,
            'focus_stop': df.focus_pstop,    
            'center_xs': center_xs,
            'center_ys': center_ys,
            'bottom': df.bottom ,
            'top': df.top,
            })
        quad = fig1.quad(bottom='bottom', top='top', left='peak_start', right='peak_stop', 
              source=source, color="gray", alpha=.1, line_width=1)
        quad2 = fig1.quad(bottom='bottom', top='top', left='focus_start', right='focus_stop', 
              source=source, color="red", alpha=.4)
        glyph = bkmod.MultiLine(xs='center_xs', ys='center_ys', line_color='red', line_width=2, line_alpha=0.8)
        fig1.add_glyph(source, glyph)
    
        hover = bkmod.HoverTool(tooltips=[
            ("Cohort", '@cohort'),
            ("Score", '@score'),
            ("Focus", "@focus_start{,} - @focus_stop{,}"),
        ], renderers=[quad])

        fig1.add_tools(hover)
    
    fig2 = ag3.plot_g123_gwss_track(
        contig=contig, 
        window_size=g123_window_size, 
        sites=phasing_analysis,
        site_mask=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig2.xaxis.visible = False

    fig3 = ag3.plot_ihs_gwss_track(
        contig=contig, 
        window_size=ihs_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig3.xaxis.visible = False


    fig4 = ag3.plot_genes(
        region=contig, 
        show=show,
        sizing_mode=sizing_mode,
        width=width,
        height=genes_height,
        x_range=fig1.x_range
        )
                        
    fig = bklay.gridplot(
        [fig1, fig2, fig3, fig4],
        ncols=1,
        toolbar_location="above",
        merge_tools=True,
        sizing_mode=sizing_mode,
    )
    return fig 

In [14]:
for contig in contigs:
    
    display(HTML(f"<h3>Chromosome {contig}</h3>"))
    
    fig = plot_h12_g123_ihs_tracks(
        contig=contig,
        df_signals=df_signals,
    );

    bkplt.show(fig)


## Sampling information

In [15]:
from ipyleaflet import Map, Marker, basemaps
from ipywidgets import HTML

center = cohort[['latitude', 'longitude']].to_list()
m = Map(center=center, zoom=9, basemap=basemaps.OpenTopoMap)

df = df_samples[['latitude', 'longitude', 'taxon']].groupby(['latitude', 'longitude', 'taxon']).size().to_frame().rename(columns={0: 'count'}).reset_index()

for coh_id, row in df.iterrows():
    lat, long = row[['latitude', 'longitude']]
    
    if row['taxon'] == 'gambiae':
        color= 'red'
    elif row['taxon'] == 'coluzzii':
        color='cadetblue'
    elif row['taxon'] == 'arabiensis':
        color='lightgreen'
    else: 
        color='gray'

    marker = Marker(location=(lat, long), draggable=False, opacity=0.7, color=color)
    m.add_layer(marker);

    message2 = HTML()
    message2.value = f"n = {row['count']}"
    marker.popup = message2

display(m)

Map(center=[11.223768292682928, -4.35639024390244], controls=(ZoomControl(options=['position', 'zoom_in_text',…

In [16]:

if min_month >= 0:
    # For this cohort we have month data, so show a breakdown of sample
    # numbers by location and month.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.pivot_table(
        index=["location", "longitude", "latitude"],
        columns="month",
        values="sample_id",
        aggfunc="count",
        fill_value=0,
    )

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude")] + 
        [("Date", pd.to_datetime(x, format="%m").month_name()) 
         for x in df_loc_dt.columns[3:]], 
    )
    df_loc_dt.columns = cols
    
else:
    # For this cohort we do not have month data, so show a breakdown of sample
    # numbers by location only.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.groupby(["location", "longitude", "latitude"]).agg({"sample_id": "count"})

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude"), ("Date", cohort.year)]
    )
    df_loc_dt.columns = cols

# Style the table.
df_loc_dt_styled = (
    df_loc_dt
    .style
    .format(precision=3)
    .set_caption("Number of samples collected.")
    .hide()
)
display(df_loc_dt_styled)    

## Diagnostics
### H12 calibration

In [17]:
display(Markdown(f"Selected window size: **{h12_window_size:,}**"))

window_sizes = (100, 200, 500, 1000, 2000, 5000, 10000, 20000)

ag3.plot_h12_calibration(
    contig=h12_calibration_contig,
    analysis=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);


Selected window size: **1,000**

### G123 Calibration

In [18]:
display(Markdown(f"Selected window size: **{g123_window_size:,}**"))

ag3.plot_g123_calibration(
    contig=h12_calibration_contig,
    sites=phasing_analysis,
    site_mask=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);

Selected window size: **500**

## Data sources

In [19]:
df_sources_style = (
    df_contributors
    .style
    .set_caption("MalariaGEN Vector Observatory partners, studies and sample sets contributing data for this cohort.")
)
df_sources_style